In [258]:
import pandas as pd
import json
import glob
import os
from tqdm import tqdm
import plotly.express as px
import re

pd.set_option('display.max_colwidth', None)

In [3]:
with open('RVG1_CLARIN/001/is1a0001_annot.json') as json_data:
    data = json.load(json_data)


print(data)

{'name': 'is1a0001', 'annotates': 'is1a0001.wav', 'sampleRate': 11025, 'levels': [{'items': [{'id': 1, 'labels': [{'name': 'bundle', 'value': ''}, {'name': 'LHD', 'value': 'Partitur 1.2.10'}, {'name': 'REP', 'value': 'Muenchen'}, {'name': 'SNB', 'value': '2'}, {'name': 'SAM', 'value': '11025'}, {'name': 'SBF', 'value': '01'}, {'name': 'SSB', 'value': '16'}, {'name': 'NCH', 'value': '1'}, {'name': 'SPN', 'value': ''}]}], 'name': 'bundle', 'type': 'ITEM'}, {'items': [{'id': 2, 'labels': [{'name': 'ORT', 'value': '2'}, {'name': 'KAN', 'value': "tsv'aI"}, {'name': 'TR2', 'value': ''}]}], 'name': 'ORT', 'type': 'ITEM'}, {'name': 'TRN', 'type': 'SEGMENT', 'items': []}, {'name': 'MAU', 'type': 'SEGMENT', 'items': []}, {'name': 'MAS', 'type': 'ITEM', 'items': []}], 'links': [{'fromID': 1, 'toID': 2}]}


In [82]:
dialects = pd.read_csv('dialects.txt', sep=",", names=['ID', 'Dialect'])
#data.columns = ["a", "b", "c", "etc."]

In [86]:
speakers = pd.read_csv('sprk_att.txt', sep=";")

In [87]:
speakers

cdnr  filenr diaclass diareg  age sex  height  weight  \
0      1      43        A     A2   30   m     183      60   
1      1      40        B     B5   28   m     184      78   
2      1      37        D     D4   26   w     149      45   
3      1      42        D     D4   23   w     167      52   
4      1      41        D     D5   23   m     206     102   
..   ...     ...      ...    ...  ...  ..     ...     ...   
495   20     507        E     E2   26   w     172      60   
496   20     511        E     E2   24   w     161      56   
497    X     330        H     H1   20   w     170      54   
498    X     331        H     H1   21   m     177      64   
499    X     332        H     H1   24   m     177      71   

                       born                    time parents  \
0                   krefeld                 krefeld      dE   
1            madrid/spanien                 münchen      dA   
2     mainhausen,.offenbach   mainhausen,.offenbach      dA   
3          fürstenfeldbruck        fürstenfeldbruck      dM   
4                  mannheim                mannheim      dA   
..                      ...                     ...     ...   
495                 leipzig                bahratal      dE   
496  elster/elbe/wittenberg  elster/elbe/wittenberg      dE   
497       lauffen/heilbronn                 lauffen      dV   
498       illingen/enzkreis       illingen/enzkreis      dE   
499               karlsruhe               karlsruhe      dE   

                               mother                            father  \
0                             krefeld                           krefeld   
1                  schlesien/bromberg                schlesien/sprottau   
2                         tokio,japan                       kyoto,japan   
3                           göttingen                           münchen   
4                                köln                         stuttgart   
..                                ...                               ...   
495                       wei"senfels                        königsberg   
496  gallin/wittenberg/sachsen-anhalt  elster/wittenberg/sachsen-anhalt   
497                         heilbronn                  albstadt/ebingen   
498                pforzheim/enzkreis           ensingen/lk.ludwigsburg   
499                         karlsruhe            italien/apulien/tarent   

     school         profession            diaself  
0    abitur  wiss.angestellter          rheinisch  
1    abitur          doktorand  hochdeutsch(nord)  
2    abitur          studentin           hessisch  
3    abitur          studentin   hochdeutsch(süd)  
4    abitur   verw..wiss..ass.      rheinländisch  
..      ...                ...                ...  
495  abitur          musikerin           gemischt  
496  abitur          studentin       elbauenslang  
497  abitur          studentin         schwäbisch  
498  abitur            student         schwäbisch  
499  abitur            student            badisch  

[500 rows x 16 columns]

In [146]:
full_dataset = []
for person in tqdm(os.listdir('RVG1_CLARIN/')):
    root_file = person
    for file in glob.glob(f'RVG1_CLARIN/{root_file}/*.wav'):
        row = {}
        row['Person ID'] = person
        row['Speechfile'] = file
        row['File ID'] = file.split('/')[-1][:-4]
        annot_file = file[:-4] + '_annot.json'
        with open(annot_file) as json_data:
            data = json.load(json_data)

        all_labels = [
        label for level in data['levels'] 
        for item in level['items'] 
        for label in item['labels']
        ]
        full_topic = ''
        for label in all_labels:
            if label['name'] == 'ORT':
                if full_topic == '':
                    full_topic = full_topic + label['value']
                else:
                    full_topic = full_topic + ' ' + label['value'] + ' '
        row['Content'] = full_topic
        full_dataset.append(row)



100%|██████████| 504/504 [03:34<00:00,  2.35it/s]


In [279]:
full_df= pd.DataFrame(full_dataset)
len(full_df)

155470

In [149]:
full_df['Person ID'] = full_df['Person ID'].astype(int)

In [150]:
merged_df = full_df.merge(speakers, how='inner', left_on='Person ID', right_on='filenr')

In [151]:
merged_df = merged_df.merge(dialects, how='left', left_on='diareg', right_on='ID')

In [153]:
merged_df.to_csv('merged_BAS_data.csv', index=False)

In [106]:
merged_df.groupby(['File ID'])['Person ID', 'Dialect'].count()

/var/folders/8g/lh2lrvsj7837bypfsr65hcb80000gn/T/ipykernel_46483/1100577298.py:1: FutureWarning: Indexing with multiple keys (implicitly converted to a tuple of keys) will be deprecated, use a list instead.
  merged_df.groupby(['File ID'])['Person ID', 'Dialect'].count()


Person ID  Dialect
File ID                     
is1a0001        497      453
is1a0002        497      453
is1a0003        496      453
is1a0004        497      453
is1a0005        497      453
...             ...      ...
t7ld0016         90       86
t7ld0017         90       86
t7ld0018         90       86
t7ld0019         90       86
t7ld0020         90       86

[2084 rows x 2 columns]

In [155]:
# Filter out outliers
test = merged_df.groupby(['File ID','Content'])['Person ID', 'Dialect'].count().sort_values(by='Person ID',ascending=True).reset_index()

/var/folders/8g/lh2lrvsj7837bypfsr65hcb80000gn/T/ipykernel_46483/213191974.py:2: FutureWarning: Indexing with multiple keys (implicitly converted to a tuple of keys) will be deprecated, use a list instead.
  test = merged_df.groupby(['File ID','Content'])['Person ID', 'Dialect'].count().sort_values(by='Person ID',ascending=True).reset_index()


In [241]:
merged_df.head()

Person ID                    Speechfile   File ID  \
0        135  RVG1_CLARIN/135/sp1a0001.wav  sp1a0001   
1        135  RVG1_CLARIN/135/st1a0253.wav  st1a0253   
2        135  RVG1_CLARIN/135/st1a0247.wav  st1a0247   
3        135  RVG1_CLARIN/135/st1a0045.wav  st1a0045   
4        135  RVG1_CLARIN/135/st1b0031.wav  st1b0031   

                                             Content cdnr  filenr diaclass  \
0  also gestern  sind  wir  um  erst  mal  relati...    7     135        F   
1        Wuenschen Sie  Raucher  oder  Nichtraucher     7     135        F   
2  Alle Kritiker  ruehmen  das  mit  grosser  Ver...    7     135        F   
3                      Ich spuere  ihn  nicht  mehr     7     135        F   
4                          Hier gibt  es  Konserven     7     135        F   

  diareg  age sex  ...                                   time  parents  \
0     F5   35   m  ...  landkreis.unterallgäu.(bei.memmingen)       dE   
1     F5   35   m  ...  landkreis.unterallgäu.(bei.memmingen)       dE   
2     F5   35   m  ...  landkreis.unterallgäu.(bei.memmingen)       dE   
3     F5   35   m  ...  landkreis.unterallgäu.(bei.memmingen)       dE   
4     F5   35   m  ...  landkreis.unterallgäu.(bei.memmingen)       dE   

                        mother       father  school profession  \
0  unterallgäu.(bei.memmingen)  unterallgäu  abitur    student   
1  unterallgäu.(bei.memmingen)  unterallgäu  abitur    student   
2  unterallgäu.(bei.memmingen)  unterallgäu  abitur    student   
3  unterallgäu.(bei.memmingen)  unterallgäu  abitur    student   
4  unterallgäu.(bei.memmingen)  unterallgäu  abitur    student   

                   diaself  ID     Dialect Content Type  
0  unterallgäür-schwäbisch  F5  Schwäbisch    only text  
1  unterallgäür-schwäbisch  F5  Schwäbisch    only text  
2  unterallgäür-schwäbisch  F5  Schwäbisch    only text  
3  unterallgäür-schwäbisch  F5  Schwäbisch    only text  
4  unterallgäür-schwäbisch  F5  Schwäbisch    only text  

[5 rows x 23 columns]

In [243]:
len(merged_df['File ID'].unique())

2084

In [181]:
single_persons = merged_df.groupby(['Person ID']).first().reset_index()

In [182]:
test = single_persons.groupby(['Dialect'])['Person ID'].count().sort_values(ascending=True).reset_index()
fig = px.bar(test, x='Dialect', y='Person ID')
fig.show()

In [191]:
test = single_persons.groupby(['Dialect', 'sex'])['Person ID'].count().sort_values(ascending=True).reset_index()
fig = px.bar(test, x='Dialect', y='Person ID', color='sex', barmode='group')
fig.show()

In [201]:
test = merged_df.groupby(['File ID'])['Dialect'].nunique().sort_values(ascending=True).reset_index()
fig = px.bar(test, x='File ID', y='Dialect')
fig.show()

In [169]:
test = merged_df.groupby(['File ID'])['Content'].count().reset_index()

In [203]:
def parse_content(row):
    if re.search(r'\d', row['Content']):
        return 'only digits'
    else:
        return 'only text'
    
    
merged_df['Content Type'] = merged_df.apply(lambda row: parse_content(row), axis=1)

In [204]:
merged_df['Content Type'].value_counts()

only text      80542
only digits    74928
Name: Content Type, dtype: int64

In [208]:
sub = merged_df[merged_df['Content Type'] == 'only digits'].groupby(['File ID'])['Dialect'].nunique().sort_values(ascending=True).reset_index()
fig = px.bar(sub, x='File ID', y='Dialect')
fig.show()

In [209]:
sub = merged_df[merged_df['Content Type'] == 'only digits'].groupby(['Content'])['Dialect'].nunique().sort_values(ascending=True).reset_index()
fig = px.bar(sub, x='Content', y='Dialect')
fig.show()

In [210]:
sub = merged_df[merged_df['Content Type'] == 'only text'].groupby(['File ID'])['Dialect'].nunique().sort_values(ascending=True).reset_index()
fig = px.bar(sub, x='File ID', y='Dialect')
fig.show()

In [211]:
sub = merged_df[merged_df['Content Type'] == 'only text'].groupby(['Content'])['Dialect'].nunique().sort_values(ascending=True).reset_index()
fig = px.bar(sub, x='Content', y='Dialect')
fig.show()

In [240]:
split_data = merged_df[merged_df['Content Type'] == 'only text'].groupby(['File ID', 'Content']).size().reset_index(name='Count')

In [239]:
fig = px.bar(
    split_data,
    x='File ID',
    y='Count',
    color='Content',  # Assign different colors to each unique value
    title="Stacked Bar Chart Showing Unique Value Distribution",
    labels={'Count': 'Count', 'Values': 'Unique Values'}
)
fig.update_layout(showlegend=False)
fig.show()

In [248]:
# 'SP = What have you done? Or explain about your day

In [281]:
split_data.groupby(['File ID']).count().sort_values(by='Count', ascending=False)[3:10]

Content  Count
File ID                 
sp1d0001      414    414
st1b0384       20     20
st1a0384       20     20
st1a0363       17     17
st1b0363       17     17
st1c0384       16     16
st1c0363       16     16

In [283]:
split_data[split_data['File ID'] == 'st1a0363']

File ID  \
3399  st1a0363   
3400  st1a0363   
3401  st1a0363   
3402  st1a0363   
3403  st1a0363   
3404  st1a0363   
3405  st1a0363   
3406  st1a0363   
3407  st1a0363   
3408  st1a0363   
3409  st1a0363   
3410  st1a0363   
3411  st1a0363   
3412  st1a0363   
3413  st1a0363   
3414  st1a0363   
3415  st1a0363   

                                                                                                                       Content  \
3399                                Kaviar ist  der  elftbeste  Slalomfahrer  oder  Xaviar  ist  der  elftbeste  Slalomfahrer    
3400                                                                             Xaver ist  der  elf  elftbeste  Slalomfahrer    
3401                                                                                  Xaver ist  der  elftbeste  Slalomfahrer    
3402                                                            Xavier <aeh>  <hm>  Xavier  ist  der  elftbeste  Slalomfahrer    
3403                                                                         Xavier Xavier  ist  der  elftbeste  Slalomfahrer    
3404                                                                                     Xavier ist  der  beste  Slalomfahrer    
3405                                                                          Xavier ist  der  beste  elftbeste  Slalomfahrer    
3406                                             Xavier ist  der  beste  elftbeste  Xavier  ist  der  elftbeste  Slalomfahrer    
3407  Xavier ist  der  beste  na  stop  muss  ich  jetzt  nochmal  eine  Leertaste  Xavier  ist  der  elftbeste  Slalomfahrer    
3408                                                    Xavier ist  der  beste  oh  Xavier  ist  der  elftbeste  Slalomfahrer    
3409                                                                           Xavier ist  der  elfs  elftbeste  Slalomfahrer    
3410                                                                    Xavier ist  der  elftbeste  Salomfahrer  Slalomfahrer    
3411                                                             Xavier ist  der  elftbeste  Sch  Slalomlaeufer  Slalomfahrer    
3412                                                                                 Xavier ist  der  elftbeste  Slalomfahrer    
3413                                                                  Xavier ist  der  elftbeste  Slalomlaeufer  Slalomfahrer    
3414                                                                      Xavier ist  der  elftbeste  elftbeste  Slalomfahrer    
3415                        Xavier ist  der  ist  der  eltbeste  Slalomfahrer  oje  Xavier  ist  der  elftbeste  Slalomfahrer    

      Count  
3399      1  
3400      1  
3401      2  
3402      1  
3403      1  
3404      1  
3405      1  
3406      1  
3407      1  
3408      1  
3409      1  
3410      1  
3411      1  
3412     47  
3413      1  
3414      1  
3415      1

In [273]:
merged_df[merged_df['File ID'] == 'st1b0384'][['Content']][50:100]

Content
116777                       Der fauler  Schueler  legte  ohne  sich  zu  schaemen  im  Gymnasium  ein  Stinkboembchen 
119667                        Der faule  Schueler  legte  ohne  sich  zu  schaemen  im  Gymnasium  ein  Stinkboembchen 
120687                        Der faule  Schueler  legte  ohne  sich  zu  schaemen  im  Gymnasium  ein  Stinkboembchen 
122897                        Der faule  Schueler  legte  ohne  sich  zu  schaemen  im  Gymnasium  ein  Stinkboembchen 
126297                        Der faule  Schueler  legte  ohne  sich  zu  schaemen  im  Gymnasium  ein  Stinkboembchen 
128507                        Der faule  Schueler  legte  ohne  sich  zu  schaemen  im  Gymnasium  ein  Stinkboembchen 
129017                        Der faule  Schueler  legte  ohne  sich  zu  schaemen  im  Gymnasium  ein  Stinkboembchen 
129527                       Der faule  Schueler  legte  ohne  sich  zu  schmaehen  im  Gymnasium  ein  Stinkboembchen 
130545                        Der faule  Schueler  legte  ohne  sich  zu  schaemen  im  Gymnasium  ein  Stinkboembchen 
137005                       Der faule  Schueler  legte  ohne  sich  zu  schaemen  im  Gymnasium  eine  Stinkboembchen 
137684  Der faule  Schueler  legte  ohne  sich  zu  schaemen  im  Gymnasium  eine  Stinkboembchen  ein  Stinkboembchen 
138194                        Der faule  Schueler  legte  ohne  sich  zu  schaemen  im  Gymnasium  ein  Stinkboembchen 
139695                        Der faule  Schueler  legte  ohne  sich  zu  schaemen  im  Gymnasium  ein  Stinkboembchen 
142060                       Der faule  Schueler  legte  ohne  sich  zu  schaemen  im  Gymnasium  eine  Stinkboembchen 
143591                  Der faule  Schueler  legte  ohne  sich  zu  schaemen  im  im  Gymnasium  ein  eine  Stinkbombe 
143930                        Der faule  Schueler  legte  ohne  sich  zu  schaemen  im  Gymnasium  ein  Stinkboembchen

In [277]:
len(merged_df)

155470

In [276]:
merged_df[merged_df['Content'].str.contains('Stinkbombe', case=False, na=False)]

Person ID                    Speechfile   File ID  \
42641          62  RVG1_CLARIN/062/st1b0384.wav  st1b0384   
42729          62  RVG1_CLARIN/062/st1c0384.wav  st1c0384   
42783          62  RVG1_CLARIN/062/st1a0384.wav  st1a0384   
42896          62  RVG1_CLARIN/062/st1d0384.wav  st1d0384   
71325         144  RVG1_CLARIN/144/st1b0384.wav  st1b0384   
71399         144  RVG1_CLARIN/144/st1c0384.wav  st1c0384   
71451         144  RVG1_CLARIN/144/st1a0384.wav  st1a0384   
71566         144  RVG1_CLARIN/144/st1d0384.wav  st1d0384   
143591        345  RVG1_CLARIN/345/st1b0384.wav  st1b0384   
143665        345  RVG1_CLARIN/345/st1c0384.wav  st1c0384   
143717        345  RVG1_CLARIN/345/st1a0384.wav  st1a0384   
143832        345  RVG1_CLARIN/345/st1d0384.wav  st1d0384   

                                                                                                                                                                                           Content  \
42641   Der faule  Schueler  legte  ohne  sich  zu  schaemen  im  Gymnasium  eine  Stinkbombe  ein  ah  Der  faule  Schueler  legte  ohne  sich  zu  schaemen  im  Gymnasium  ein  Stinkboembchen    
42729   Der faule  Schueler  legte  ohne  sich  zu  schaemen  im  Gymnasium  eine  Stinkbombe  ein  ah  Der  faule  Schueler  legte  ohne  sich  zu  schaemen  im  Gymnasium  ein  Stinkboembchen    
42783   Der faule  Schueler  legte  ohne  sich  zu  schaemen  im  Gymnasium  eine  Stinkbombe  ein  ah  Der  faule  Schueler  legte  ohne  sich  zu  schaemen  im  Gymnasium  ein  Stinkboembchen    
42896   Der faule  Schueler  legte  ohne  sich  zu  schaemen  im  Gymnasium  eine  Stinkbombe  ein  ah  Der  faule  Schueler  legte  ohne  sich  zu  schaemen  im  Gymnasium  ein  Stinkboembchen    
71325                                                                                                 Der faule  Schueler  hat  ohne  sich  zu  schaemen  im  Gymnasium  eine  Stinkbombe  gelegt    
71399                                                                                                 Der faule  Schueler  hat  ohne  sich  zu  schaemen  im  Gymnasium  eine  Stinkbombe  gelegt    
71451                                                                                                 Der faule  Schueler  hat  ohne  sich  zu  schaemen  im  Gymnasium  eine  Stinkbombe  gelegt    
71566                                                                                                 Der faule  Schueler  hat  ohne  sich  zu  schaemen  im  Gymnasium  eine  Stinkbombe  gelegt    
143591                                                                                             Der faule  Schueler  legte  ohne  sich  zu  schaemen  im  im  Gymnasium  ein  eine  Stinkbombe    
143665                                                                                             Der faule  Schueler  legte  ohne  sich  zu  schaemen  im  im  Gymnasium  ein  eine  Stinkbombe    
143717                                                                                             Der faule  Schueler  legte  ohne  sich  zu  schaemen  im  im  Gymnasium  ein  eine  Stinkbombe    
143832                                                                                             Der faule  Schueler  legte  ohne  sich  zu  schaemen  im  im  Gymnasium  ein  eine  Stinkbombe    

       cdnr  filenr diaclass diareg  age sex  ...               time  parents  \
42641     2      62        D     D1   26   m  ...  kleinich/hunsrück       dE   
42729     2      62        D     D1   26   m  ...  kleinich/hunsrück       dE   
42783     2      62        D     D1   26   m  ...  kleinich/hunsrück       dE   
42896     2      62        D     D1   26   m  ...  kleinich/hunsrück       dE   
71325     7     144        F     F3   21   w  ...             zürich       dE   
71399     7     144        F     F3   21   w  ...             zürich       dE   
71451     7     144        F     F3   21   w  ...             zürich    

In [275]:
type(merged_df['Content'][0])

str

In [ ]:
# Count occurrences of each unique value per category
split_data = merged_df[merged_df['Content Type'] == 'only text'].groupby(['Content', 'Dialect']).size().reset_index(name='Count')

# Create a stacked bar chart


fig.show()

In [226]:
merged_df[['Dialect', 'File ID', 'Content']]

Dialect   File ID  \
0          Schwäbisch  sp1a0001   
1          Schwäbisch  st1a0253   
2          Schwäbisch  st1a0247   
3          Schwäbisch  st1a0045   
4          Schwäbisch  st1b0031   
...               ...       ...   
155465  Obersächsisch  st1a0074   
155466  Obersächsisch  stdc0010   
155467  Obersächsisch  st1a0276   
155468  Obersächsisch  is2a0017   
155469  Obersächsisch  is2a0003   

                                                  Content  
0       also gestern  sind  wir  um  erst  mal  relati...  
1             Wuenschen Sie  Raucher  oder  Nichtraucher   
2       Alle Kritiker  ruehmen  das  mit  grosser  Ver...  
3                           Ich spuere  ihn  nicht  mehr   
4                               Hier gibt  es  Konserven   
...                                                   ...  
155465                 Vater mischt  gleich  die  Karten   
155466                    0 3  5  1  3  5  3  4  5  5  4   
155467        Hermann traegt  einen  zweireihigen  Anzug   
155468                                                 50  
155469                                            zwoelfs  

[155470 rows x 3 columns]